In [1]:
!pip install ipynb
!pip install pymongo
!pip install requests
!pip install fsspec
!pip install pandas
!pip install quandl
!pip install matplotlib
!pip install httplib2
!pip install seaborn
!pip install dash
!pip install time
!pip install geojson
!pip install plotly-geo
!pip install geopandas==0.8.1
!pip install pyshp==1.2.10
!pip install shapely==1.6.3
!pip install xlrd
!pip install sklearn
!pip3 install PyQt5==5.9.2
!pip install openpyxl
!pip install charmap
!pip install pyowm

ERROR: Could not find a version that satisfies the requirement time
ERROR: No matching distribution found for time


ERROR: Could not find a version that satisfies the requirement charmap
ERROR: No matching distribution found for charmap


In [2]:
import pymongo
import requests
import threading
import os
import time
from datetime import datetime
import shutil
import json
import matplotlib
import httplib2
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import geopandas
import shapely
import shapefile
import plotly
from plotly.figure_factory._county_choropleth import create_choropleth
import xlrd
import pyowm

In [52]:
import pandas as pd
import json
import requests

api_key_weather = '4ec6d8294cc035f9984915415bf61ca3'

#api.openweathermap.org/data/2.5/weather?q=London&appid={API key}

api_url = "http://api.openweathermap.org/data/2.5/weather?"
storelocations_path = "D://Shital/NCI DA/DataBase/CA2/Starbucks_Project/Starbucks_Locations/directory.csv"

In [4]:
#reading CSV file into dataframe
starbucks_storedata = pd.read_csv(storelocations_path)
#starbucks_storedata.head()

In [5]:
#creating dataframe containing starbucks brand only
starbucks_df = starbucks_storedata[starbucks_storedata["Brand"].isin(["Starbucks"])]
#starbucks_df.head()

In [6]:
#creating dataframe with number of countries
starbucks_countries = starbucks_df[starbucks_df["Country"].isin(["AD","AE","AR","AT","AU","AW","AZ","BE","BG","BN","BO","BR","CA","CN","CO","CR","CW","CY","CZ","DE","DK","EG","ES","FI","FR","GB","GR","HU","ID","IE","IN","JP","KR","KW","KZ","LB","LU","MA","MX","NL","NO","PA","PE","PR","PT","QA","RO","RU","SA","SE","SG","SK","SV","TH","TR","TT","TW","US","VN","ZA"])]
#starbucks_countries.head()

In [7]:
#removing missing values
starbucks_countries = starbucks_countries.dropna(subset = ["Postcode"])
# starbucks_countries.head()


In [8]:
#creating list of cities present in starbucks_countries
starbucks_cities = starbucks_countries["City"].unique()

# starbucks_cities


In [9]:
#Creating dataframe to store data collected using API

df = pd.DataFrame(columns=['city_name', 'city_lat', 'city_lng', 'city_temp_max','city_temp_min','city_temp','city_pressure', 'city_humidity', 'city_cloud', 'city_wind_speed','city_wind_deg', 'city_country', 'city_date', 'city_sunrise', 'city_sunset','weather_main','weather_description'])
print(df)

Empty DataFrame
Columns: [city_name, city_lat, city_lng, city_temp_max, city_temp_min, city_temp, city_pressure, city_humidity, city_cloud, city_wind_speed, city_wind_deg, city_country, city_date, city_sunrise, city_sunset, weather_main, weather_description]
Index: []


In [10]:
#To get weather forecasting based on a city Name using API

import requests, json
  
# To enter API Key
api_key = "cb7b06cb810fa129917a70b66ace5a45"
  
# creating variable to store URL
base_url = "http://api.openweathermap.org/data/2.5/weather?"
  
# Enter City Name to get weather forecast
city_name = input("Enter city name : ")
  
# creating variable to store complete variable
complete_url = base_url + "appid=" + api_key + "&q=" + city_name
  
# defining request module which rerurns response object

response = requests.get(complete_url)

#Converting json format data into python format data

x = response.json()
  
# If value of cod =404 means city not found
if x["cod"] != "404":
  
    # Defining variable y to store the value of "main" key
    y = x["main"]
  
    # Defining variable to store the value corresponding to the "temp" key of y
    current_temperature = y["temp"]
  
    # Defining variable to store the value corresponding to the "pressure" key of y
    current_pressure = y["pressure"]
  
    # Defining variable to store the value corresponding to the "humidity" key of y
    current_humidiy = y["humidity"]
  
    #  Defining variable to store store the value of "weather" key in variable z
    z = x["weather"]
  
    # Defining variable to store the value corresponding to the "description" key at the 0th index of z
    weather_description = z[0]["description"]
  
    # To print following values
    print(" Temperature (in kelvin unit) = " +
                    str(current_temperature) + 
          "\n atmospheric pressure (in hPa unit) = " +
                    str(current_pressure) +
          "\n humidity (in percentage) = " +
                    str(current_humidiy) +
          "\n description = " +
                    str(weather_description))
  
else:
    print(" City Not Found ")

Enter city name : Dubai
 Temperature (in kelvin unit) = 303.5
 atmospheric pressure (in hPa unit) = 1008
 humidity (in percentage) = 23
 description = clear sky


In [11]:
#Collecting data using API and storing in csv file

import json
from pymongo import MongoClient
import httplib2
# Making a Connection with MongoClient
client = MongoClient("mongodb://localhost:27017/")
# database
db = client["Weather_Starbucks_Location_DB"]
# collection
company= db["Weather_Data"]

api_key = api_key_weather

def weather_data(count):
    i = 0    
    for city in starbucks_cities:
        print(i, end='\r')
        query_url = api_url + "appid=" + api_key + "&q=" + city + "&units=metric"
        city_info = requests.get(query_url).json()
         
        try:
            city_info = requests.get(query_url).json()
            df.loc[i,'city_name'] = city_info["name"]
            df.loc[i,'city_lat'] = city_info["coord"]["lat"]
            df.loc[i,'city_lng'] = city_info["coord"]["lon"]
            df.loc[i,'city_temp_max'] = city_info["main"]["temp_max"]
            df.loc[i,'city_temp'] = city_info["main"]["temp"]
            df.loc[i,'city_temp_min'] = city_info["main"]["temp_min"]
            df.loc[i,'city_pressure'] = city_info["main"]["pressure"]
            df.loc[i,'city_humidity'] = city_info["main"]["humidity"]
            df.loc[i,'city_cloud'] = city_info["clouds"]["all"]
            df.loc[i,'city_wind_speed'] = city_info["wind"]["speed"]
            df.loc[i,'city_wind_deg'] = city_info["wind"]["deg"]
            df.loc[i,'city_country'] = city_info["sys"]["country"]
            df.loc[i,'city_date'] = city_info["dt"]
            df.loc[i,'city_sunrise'] = city_info["sys"]["sunrise"]
            df.loc[i,'city_sunset'] = city_info["sys"]["sunset"]
            df.loc[i,'weather_main'] = city_info["weather"][0]["main"]
            df.loc[i,'weather_description'] = city_info["weather"][0]["description"]
            df.to_csv('{}.csv'.format("Weather_Data"), index=False)
            
        except(KeyError):
            print("City not found")
        i=i+1
        if i > count:
            break
        else:
            pass

    print("Weather Data Complete")
        

In [53]:
weather_data(count=50000)
# time.sleep(3600)

City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not found
City not f

ConnectionError: HTTPConnectionPool(host='api.openweathermap.org', port=80): Max retries exceeded with url: /data/2.5/weather?appid=cb7b06cb810fa129917a70b66ace5a45&q=Little%20Ferry&units=metric (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000025738023188>: Failed to establish a new connection: [WinError 10060] A connection attempt failed because the connected party did not properly respond after a period of time, or established connection failed because connected host has failed to respond'))

In [54]:
#Importing data into MongoDB

from pymongo import MongoClient
import pandas as pd
import json
 
db = MongoClient("mongodb://localhost:27017/")

def csv_to_json(filename, header=None):
    data = pd.read_csv(filename, header=header)
    return data.to_dict('records')
 
pos_col = db["Weather_Starbucks_Location_DB"]   # collection instance
 
df = pd.read_csv(r'C:\Users\ShitalRaut\Downloads\Weather_Data.csv')
 
db.Weather_Starbucks_Location_DB.Weather_Data.insert_many(csv_to_json(r'C:\Users\ShitalRaut\Downloads\Weather_Data.csv', header=0))
print("Your CSV file Imported Successfully")

Your CSV file Imported Successfully


In [55]:
#Extracting data from mongo DB

from pymongo import MongoClient
import time
from datetime import datetime

client = pymongo.MongoClient("mongodb://localhost:27017/")
db = client["Weather_Starbucks_Location_DB"]
col = db["Weather_Data"]
allWeatherData = col.find()

allWeatherDict = {}
dfAllWeatherData = pd.DataFrame(list(allWeatherData))

#print(dfAllWeatherData)

#To get total number of rows and columns in data

RowCount, ColCount = dfAllWeatherData.shape
print(f'There are {RowCount} rows and {ColCount} columns')

There are 3430 rows and 18 columns


In [56]:
#Conversion of date and time formats and storing into dataframe

dfAllWeatherData.TimeStamp= pd.to_datetime(dfAllWeatherData.city_date)
dfAllWeatherData.SunriseTime= pd.to_datetime(dfAllWeatherData.city_sunrise)
dfAllWeatherData.SunsetTime= pd.to_datetime(dfAllWeatherData.city_sunset)

dfAllWeatherData['TimeStamp']= pd.to_datetime(dfAllWeatherData.city_date)
dfAllWeatherData['SunriseTime']= pd.to_datetime(dfAllWeatherData.city_sunrise)
dfAllWeatherData['SunsetTime']= pd.to_datetime(dfAllWeatherData.city_sunset)

#print(dfAllWeatherData)

C:\Users\ShitalRaut\anaconda3\envs\weather-analysis\lib\site-packages\ipykernel_launcher.py:3: UserWarning:

Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access

C:\Users\ShitalRaut\anaconda3\envs\weather-analysis\lib\site-packages\ipykernel_launcher.py:4: UserWarning:

Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access

C:\Users\ShitalRaut\anaconda3\envs\weather-analysis\lib\site-packages\ipykernel_launcher.py:5: UserWarning:

Pandas doesn't allow columns to be created via a new attribute name - see https://pandas.pydata.org/pandas-docs/stable/indexing.html#attribute-access



In [57]:
#Renaming column names

old_names = ["city_name","city_country","city_date","city_lat","city_lng","city_temp","city_temp_min","city_temp_max", "city_pressure","city_humidity","city_cloud","city_wind_speed","city_wind_deg","city_sunrise","city_sunset","TimeStamp","SunriseTime","SunsetTime","weather_main","weather_description"]
new_names = ["name","country","date","latitude","longitude","avg_temp","min_temp","max_temp","pressure","humidity","cloudiness","wind_speed","wind_deg","sunrise","sunset","timestamp","sunrise_time","sunset_time","weather_main","weather_description"]
dfAllWeatherData.rename(columns=dict(zip(old_names, new_names)), inplace=True)

#print(dfAllWeatherData)

In [59]:
#Updating order of columns in dataset

updated_column_order = ["name","country","date","timestamp","weather_main","weather_description","latitude","longitude","avg_temp","min_temp","max_temp","pressure","humidity","cloudiness","wind_speed","wind_deg","sunrise","sunrise_time","sunset","sunset_time"]
dfAllWeatherData = dfAllWeatherData[updated_column_order]
#print(dfAllWeatherData)



In [60]:
#Selecting only few columns of interest
selected_columns = ["name","country","timestamp","weather_main","weather_description","latitude","longitude","avg_temp","max_temp","pressure","humidity","cloudiness","wind_speed","sunrise_time","sunset_time"]
cityData=dfAllWeatherData[selected_columns]
#print(cityData)

In [61]:
#Checking for NULL Values using notnull() function which returns dataframe of Boolean values which are False for NaN values.

#cityData.notnull()

#To get total number of rows and columns in data which are not NULL
RowCount, ColCount = cityData.shape
print(f'There are {RowCount} rows and {ColCount} columns')

There are 3430 rows and 15 columns


In [62]:
#Exploratory data analysis on columns CityName,CityCountry,Latitude and Longitude

from mpl_toolkits.mplot3d import Axes3D
from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt # plotting
matplotlib.use('TkAgg')
import numpy as np # linear algebra
import os # accessing directory structure
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

#Selecting columns CityName,CityCountry,Latitude and Longitude

Selected_Columns= ["name","country","latitude","longitude"]
DataAnalysis = cityData[Selected_Columns]
#print(DataAnalysis)

# Distribution graphs (histogram/bar graph) of column data
def plotPerColumnDistribution(DataAnalysis, nGraphShown, nGraphPerRow):
    nunique = DataAnalysis.nunique()
    DataAnalysis = DataAnalysis[[col for col in DataAnalysis if nunique[col] > 1 and nunique[col] < 50]] # For displaying purposes, pick columns that have between 1 and 50 unique values
    nRow, nCol = DataAnalysis.shape
    columnNames = list(DataAnalysis)
    nGraphRow = (nCol + nGraphPerRow - 1) / nGraphPerRow
    plt.figure(num = None, figsize = (6 * nGraphPerRow, 8 * nGraphRow), dpi = 80, facecolor = 'w', edgecolor = 'k')
    for i in range(min(nCol, nGraphShown)):
        plt.subplot(nGraphRow, nGraphPerRow, i + 1)
        columnDf = df.iloc[:, i]
        if (not np.issubdtype(type(columnDf.iloc[0]), np.number)):
            valueCounts = columnDf.value_counts()
            valueCounts.plot.bar()
        else:
            columnDf.hist()
        plt.ylabel('counts')
        plt.xticks(rotation = 90)
        plt.title(f'{columnNames[i]} (column {i})')
    plt.tight_layout(pad = 1.0, w_pad = 1.0, h_pad = 1.0)
    plt.show()
    
    # Save Figure
    plt.savefig("D:/Shital/NCI DA/DataBase/CA2/Plots")

plotPerColumnDistribution(DataAnalysis, 10, 5)



In [63]:
import matplotlib.pyplot as plt
# Build Scatter Plot for Each Data Type
plt.scatter(cityData["latitude"], cityData["avg_temp"], facecolors="red", marker="o", edgecolor="black")

# Incorporate Other Graph Properties
plt.title("City Latitude vs. Max Temperature")
plt.ylabel("Max Temperature (°F)")
plt.xlabel("Latitude")
plt.grid(True)

# Save Figure
plt.savefig("D:/Shital/NCI DA/DataBase/CA2/Plots/ProjectCity_Latitude_vs_Max_Temperature.png")

# Show Plot
plt.show()

In [65]:
import plotly.express as px
#df = cityData.tips()
fig = px.histogram(cityData, x="avg_temp", y="humidity", color="humidity")
fig.show()

In [66]:
#Latitude Vs Temperature Plot

#Plot Latitude Data Versus Maximum Temperature Data
import plotly.express as px

output_plot= "D://Shital/NCI DA/DataBase/CA2/Plots/Maximum_Temperature_vs_City_Latitude.png"
F1, AX1 = plt.subplots()
AX1.scatter(cityData['latitude'], cityData['max_temp'], facecolor = 'blue', edgecolor = 'black')
AX1.grid()
AX1.set_title('Maximum Temperature vs City Latitude')
AX1.set_xlabel('City Latitude')
AX1.set_ylabel('Max Temp (F)')
plt.savefig(output_plot)
plt.show()


In [67]:
import plotly.express as px

fig = px.line(cityData, x="name", y="cloudiness", color="country",
              line_group="country", hover_name="name")
fig.show()

In [68]:
import plotly.express as px

#fig = px.bar(cityData, x=["clear sky","light snow","light rain","snow","mist","haze","fog","dust","smoke"], y=["AE","JP","FR","US","CA","GB","CN","DE","IN"], title="Wide-Form Input")
#fig.show()

fig = px.area(cityData, x="weather_description", y="country", color="name",
    line_group="weather_description")
fig.show()

In [69]:
#Latitude vs WeatherDescription for city
fig = px.line(cityData, x="weather_description", y="latitude", color="country",
              line_group="country", hover_name="country")
fig.show()

In [70]:
import plotly.express as px
#df = px.data.gapminder()

fig = px.scatter(cityData.query('weather_main == \"Clouds\"'), x="cloudiness", y="name",
        size="wind_speed", color="name",
                 hover_name="name", log_x=True, size_max=100)
fig.show()

In [71]:
import plotly.express as px
#df = px.data.gapminder()
fig = px.scatter(cityData, x="latitude", y="humidity", animation_frame="weather_main", animation_group="country",
           size="humidity", color="country", hover_name="name", 
           log_x=True, size_max=45, range_x=[100,100000], range_y=[25,90])
fig.show()

In [32]:
import plotly.express as px
import pandas as pd
fig = px.density_mapbox(cityData, lat='latitude', lon='longitude',  radius=10,
                        center=dict(lat=0, lon=180), zoom=0,
                        mapbox_style="stamen-terrain")
fig.show()


In [36]:
import plotly.express as px
# This dataframe has 244 lines, but 4 distinct values for `day`
#df = px.data.tips()
fig = px.pie(cityData, values='weather_description', names='weather_main')
fig.show()